In [164]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import plotly.express as px
import statistics as st

def get_df(day):
    file_name = f"./round-4-island-data-bottle/prices_round_4_day_{day}.csv"
    return pd.read_csv(file_name, sep=';')

def get_product(df, product):
    return df[df['product'] == product].copy()

def get_first_two_dfs():
    first_df = get_df(1)
    second_df = get_df(2)
    second_df['timestamp'] = second_df['timestamp'] + 1000000
    return pd.concat([first_df, second_df])



In [166]:
df = get_first_two_dfs()

In [167]:

df_coconut = get_product(df, 'COCONUT')
df_coconut_call = get_product(df, "COCONUT_COUPON")
df_coconut_call = df_coconut_call.merge(df_coconut[['timestamp', 'mid_price']], on='timestamp', suffixes=('', '_coconut'))


In [125]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_coconut['timestamp'], y=df_coconut['mid_price'], name='Coconut Mid Price'))
fig.add_trace(go.Scatter(x=df_coconut_call['timestamp'], y=df_coconut_call['mid_price'], name='Coconut Call Mid Price', yaxis='y2'))
fig.update_layout(title='Coconut and Coconut Call Prices over Timestamp', yaxis=dict(title='Coconut Mid Price'), yaxis2=dict(title='Coconut Call Bid Price', overlaying='y', side='right'))
fig.show()


In [236]:
import numpy as np
from scipy.stats import norm
from scipy.optimize import brentq

def black_scholes_call(spot, strike, time_to_expiry, volatility):
    d1 = (np.log(spot / strike) + (0.5 * volatility ** 2) * time_to_expiry) / (volatility * np.sqrt(time_to_expiry))
    d2 = d1 - volatility * np.sqrt(time_to_expiry)
    call_price = (spot * norm.cdf(d1) - strike * norm.cdf(d2))
    return call_price

def black_scholes_put(spot, strike, time_to_expiry, volatility):
    d1 = (np.log(spot / strike) + (0.5 * volatility ** 2) * time_to_expiry) / (volatility * np.sqrt(time_to_expiry))
    d2 = d1 - volatility * np.sqrt(time_to_expiry)
    put_price = (strike * norm.cdf(-d2) - spot * norm.cdf(-d1))
    return put_price

def delta(spot, strike, time_to_expiry, volatility):
    d1 = (np.log(spot) - np.log(strike) + (0.5 * volatility ** 2) * time_to_expiry) / (volatility * np.sqrt(time_to_expiry))
    return norm.cdf(d1)

def gamma(spot, strike, time_to_expiry, volatility):
    d1 = (np.log(spot) - np.log(strike) + (0.5 * volatility ** 2) * time_to_expiry) / (volatility * np.sqrt(time_to_expiry))
    return norm.pdf(d1)/(spot * volatility * np.sqrt(time_to_expiry))

def vega(spot, strike, time_to_expiry, volatility):
    d1 = (np.log(spot) - np.log(strike) + (0.5 * volatility ** 2) * time_to_expiry) / (volatility * np.sqrt(time_to_expiry))
    return norm.pdf(d1) * (spot * np.sqrt(time_to_expiry)) / 100

def implied_volatility(call_price, spot, strike, time_to_expiry):
    # Define the equation where the root is the implied volatility
    def equation(volatility):
        estimated_price = black_scholes_call(spot, strike, time_to_expiry, volatility)
        return estimated_price - call_price

    # Using Brent's method to find the root of the equation
    implied_vol = brentq(equation, 1e-10, 3.0, xtol=1e-10)
    return implied_vol

def realized_vol(df_coconut_call, window, step_size):
    df_coconut_call[f'log_return_{step_size}'] = np.log(df_coconut_call['mid_price_coconut'].to_numpy()/df_coconut_call['mid_price_coconut'].shift(step_size).to_numpy())
    dt = step_size / 250 / 10000 
    df_coconut_call[f'realized_vol_{step_size}'] = df_coconut_call[f'log_return_{step_size}'].rolling(window=window).apply(lambda x: np.mean(x[::step_size]**2) / dt)
    df_coconut_call[f'realized_vol_{step_size}'] = np.sqrt(df_coconut_call[f'realized_vol_{step_size}'].to_numpy())
    return df_coconut_call



In [237]:
spot_price = 10000        # Spot price of the underlying asset
strike_price = 10000      # Strike price of the option
call_price = 637.5         # Market price of the call option
time_to_expiry = 1      # Time to expiry in years
initial_guess = 16
df_coconut_call['implied_vol'] = df_coconut_call.apply(lambda row: implied_volatility(row['mid_price'], row['mid_price_coconut'], strike_price, time_to_expiry), axis=1)
df_coconut_call['delta'] = df_coconut_call.apply(lambda row: delta(row['mid_price_coconut'], strike_price, time_to_expiry, row['implied_vol']), axis=1)
df_coconut_call['gamma'] = df_coconut_call.apply(lambda row: gamma(row['mid_price_coconut'], strike_price, time_to_expiry, row['implied_vol']), axis=1)
df_coconut_call['vega'] = df_coconut_call.apply(lambda row: vega(row['mid_price_coconut'], strike_price, time_to_expiry, row['implied_vol']), axis=1)

In [212]:
import plotly.express as px

fig = px.line(df_coconut_call, x='timestamp', y='delta', title='Delta over Time')
fig.show()


In [238]:
fig = px.line(df_coconut_call, x='timestamp', y='vega', title='Vega over Time')
fig.show()

In [239]:
fig = px.line(df_coconut_call, x='timestamp', y='implied_vol', title='Implied Volatility over Time')
fig.show()
